## Notebook | MLlib, Fake News Prediction
Here we will be using comparing the fit of two machine learning models to predict fake news 
It must be mentioned here that we cannot evaluate the predictions we make on the test set since we do not have the true labels for the news - whether they happen to be fake or not. Therefore, although we did see the test set in previous notebooks, we have now removed it. We therefore split the training set into train and test sets in order to be evaluate the quality of our predictions.

**Note : Encoding of the target**
1. fake news = 1
2. true news = 0

### I. Loading the data and prerequisites

In [0]:
# Basic aggregation functions
import pyspark.sql.functions as F
from pyspark.sql.functions import isnan, when, count, col
from pyspark.sql.functions import round 


# Text preprocessing
# !pip install nltk
import nltk
nltk.download("stopwords")
from pyspark.sql.types import*
from pyspark.sql import SparkSession
from pyspark.sql.functions import udf, col, lower, regexp_replace
from pyspark.ml.feature import Tokenizer, StopWordsRemover
from nltk.stem.snowball import SnowballStemmer

# MLlib
from pyspark.mllib.regression import LabeledPoint
from pyspark.ml.feature import HashingTF, IDF, Tokenizer
from pyspark.mllib.classification import LogisticRegressionWithSGD
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator



In [0]:
# File location and type
file_location_1 = "/FileStore/tables/pd_train.csv"
file_location_2 = "/FileStore/tables/test.csv"
file_type = "csv"

# CSV options
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
train_df = spark.read.format(file_type) \
  .option("multiLine", True)\
  .option("header", True)\
  .option("escape", "\"")\
  .option("sep", delimiter) \
  .load(file_location_1)

display(train_df)

# # The applied options are for CSV files. For other file types, these will be ignored.
# test_df = spark.read.format(file_type) \
#   .option("multiLine", True)\
#   .option("header", True)\
#   .option("escape", "\"")\
#   .option("sep", delimiter) \
#   .load(file_location_2)

# display(test_df)

_c0 id title author text label 0 0 House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It Darrell Lucus House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It By Darrell Lucus on October 30, 2016 Subscribe Jason Chaffetz on the stump in American Fork, Utah ( image courtesy Michael Jolley, available under a Creative Commons-BY license) 
With apologies to Keith Olbermann, there is no doubt who the Worst Person in The World is this week–FBI Director James Comey. But according to a House Democratic aide, it looks like we also know who the second-worst person is as well. It turns out that when Comey sent his now-infamous letter announcing that the FBI was looking into emails that may be related to Hillary Clinton’s email server, the ranking Democrats on the relevant committees didn’t hear about it from Comey. They found out via a tweet from one of the Republican committee chairmen. 
As we now know, Comey notified the Republican chairmen and Democratic ranking members of the House Intelligence, Judiciary, and Oversight committees that his agency was reviewing emails it had recently discovered in order to see if they contained classified information. Not long after this letter went out, Oversight Committee Chairman Jason Chaffetz set the political world ablaze with this tweet. FBI Dir just informed me, "The FBI has learned of the existence of emails that appear to be pertinent to the investigation." Case reopened 
— Jason Chaffetz (@jasoninthehouse) October 28, 2016 
Of course, we now know that this was not the case . Comey was actually saying that it was reviewing the emails in light of “an unrelated case”–which we now know to be Anthony Weiner’s sexting with a teenager. But apparently such little things as facts didn’t matter to Chaffetz. The Utah Republican had already vowed to initiate a raft of investigations if Hillary wins–at least two years’ worth, and possibly an entire term’s worth of them. Apparently Chaffetz thought the FBI was already doing his work for him–resulting in a tweet that briefly roiled the nation before cooler heads realized it was a dud. 
But according to a senior House Democratic aide, misreading that letter may have been the least of Chaffetz’ sins. That aide told Shareblue that his boss and other Democrats didn’t even know about Comey’s letter at the time–and only found out when they checked Twitter. “Democratic Ranking Members on the relevant committees didn’t receive Comey’s letter until after the Republican Chairmen. In fact, the Democratic Ranking Members didn’ receive it until after the Chairman of the Oversight and Government Reform Committee, Jason Chaffetz, tweeted it out and made it public.” 
So let’s see if we’ve got this right. The FBI director tells Chaffetz and other GOP committee chairmen about a major development in a potentially politically explosive investigation, and neither Chaffetz nor his other colleagues had the courtesy to let their Democratic counterparts know about it. Instead, according to this aide, he made them find out about it on Twitter. 
There has already been talk on Daily Kos that Comey himself provided advance notice of this letter to Chaffetz and other Republicans, giving them time to turn on the spin machine. That may make for good theater, but there is nothing so far that even suggests this is the case. After all, there is nothing so far that suggests that Comey was anything other than grossly incompetent and tone-deaf. 
What it does suggest, however, is that Chaffetz is acting in a way that makes Dan Burton and Darrell Issa look like models of responsibility and bipartisanship. He didn’t even have the decency to notify ranking member Elijah Cummings about something this explosive. If that doesn’t trample on basic standards of fairness, I don’t know what does. 
Granted, it’s not likely that Chaffetz will have to answer for this. He sits in a ridiculously Republican district anchored in Provo and Orem; it has a Cook

id title author text 20800 Specter of Trump Loosens Tongues, if Not Purse Strings, in Silicon Valley - The New York Times David Streitfeld PALO ALTO, Calif. — After years of scorning the political process, Silicon Valley has leapt into the fray. The prospect of a President Donald J. Trump is pushing the tech community to move beyond its traditional role as donors and to embrace a new existence as agitators and activists. A distinguished venture capital firm emblazoned on its corporate home page an earthy epithet. One prominent tech chieftain says the consequences of Mr. Trump’s election would “range between disastrous and terrible. ” Another compares him to a dictator. And nearly 150 tech leaders signed an open letter decrying Mr. Trump and his campaign of “anger” and “bigotry. ” Not quite all the action is . Peter Thiel, a founder of PayPal and Palantir who was the first outside investor in Facebook, spoke at the Republican convention in July. The New York Times reported on Saturday that Mr. Thiel is giving $1. 25 million to support Mr. Trump’s candidacy even as other supporters flee. (He also recently gave $1 million to a “super PAC” that supports Senator Rob Portman, the Republican freshman running for in Ohio.) Getting involved in politics used to be seen as clashing with Silicon Valley’s value system: You transform the world by making problems obsolete, not solving them through Washington. Nor did entrepreneurs want to alienate whatever segment of customers did not agree with them politically. Such reticence is no longer in style here. “We’re a bunch of nerds not used to having a lot of limelight,” said Dave McClure, an investor who runs a tech incubator called 500 Startups. “But to quote ‘With great power comes great responsibility. ’” Mr. McClure grew worried after the Republican and Democratic conventions as Mr. Trump began to catch up to Hillary Clinton in the polls. He wanted Silicon Valley to do more, and so late last month he announced Nerdz4Hillary, an informal effort. An initial group of donors pledged $50, 000 the goal was to ask the “nerdz” for small donations to match that sum. They have not come through yet. “We’re kind of optimistic we’ll get the other $50, 000 in a few weeks,” Mr. McClure said. That relatively slow pace reflects Silicon Valley’s shifting position: Even as it becomes increasingly free with its opinions, it has been less free with its checkbook. The most recent data, from late August, shows Mrs. Clinton taking in $7. 7 million from the tech community, according to Crowdpac, a that tracks donations. By that point in 2012, Crowdpac says, President Obama had raised $21 million from entrepreneurs and venture capitalists. Reid Hoffman, the billionaire of the business networking site LinkedIn, offers a snapshot of Silicon Valley’s evolving approach to politics. Mr. Hoffman was a top Obama donor, giving $1 million to the Priorities USA political action committee, something several of his peers did as well. Last month, Mr. Hoffman garnered worldwide publicity for saying he would donate up to $5 million to veterans’ groups if Mr. Trump released his taxes, a remote possibility that never came to pass. He has castigated Mr. Trump in interviews, saying he was speaking for those who were afraid. Mr. Hoffman’s outright donations, however, have been smaller this election cycle. In May, he gave $400, 000 to the Hillary Victory Fund. Asked if there was more recent giving that had not shown up in federal election records, Mr. Hoffman cryptically responded in an email, “Looking at some PACs, etc. ” He declined several opportunities to elaborate. Even as Priorities USA has raised $133 million this election cycle, far exceeding its total in 2012, its tech contributions have dwindled. The only familiar tech name this time around is John Doerr of the venture capital firm Kleiner Perkins Caufield Byers, who gave $500, 000. The AOL Steve Case said his September endorsement of Mrs. Clinton, via an in The Washington Po

### II. Some preliminary cleaning !

In [0]:
# Display schema and data sample
train_df.printSchema()
train_df.show(3)

# test_df.printSchema()
# test_df.show(3)

print("Number of unique articles in training set: {}".format(train_df.select('id').distinct().count()))
# print("Number of unique articles in test set: {}".format(test_df.select('id').distinct().count()))

root
-- _c0: string (nullable = true)
-- id: string (nullable = true)
-- title: string (nullable = true)
-- author: string (nullable = true)
-- text: string (nullable = true)
-- label: string (nullable = true)

+---+---+--------------------+------------------+--------------------+-----+
_c0| id| title| author| text|label|
+---+---+--------------------+------------------+--------------------+-----+
 0| 0|House Dem Aide: W...| Darrell Lucus|House Dem Aide: W...| 1|
 1| 1|FLYNN: Hillary Cl...| Daniel J. Flynn|Ever get the feel...| 0|
 2| 2|Why the Truth Mig...|Consortiumnews.com|Why the Truth Mig...| 1|
+---+---+--------------------+------------------+--------------------+-----+
only showing top 3 rows

root
-- id: string (nullable = true)
-- title: string (nullable = true)
-- author: string (nullable = true)
-- text: string (nullable = true)

+-----+--------------------+----------------+--------------------+
 id| title| author| text|
+-----+--------------------+----------------+--------------------+
20800|Specter of Trump ...|David Streitfeld|PALO ALTO, Calif....|
20801|Russian warships ...| nan|Russian warships ...|
20802|#NoDAPL: Native A...| Common Dreams|Videos #NoDAPL: N...|
+-----+--------------------+----------------+--------------------+
only showing top 3 rows

Number of unique articles in training set: 20800
Number of unique articles in test set: 5200

In [0]:
train_df.select([count(when(isnan(c), c)).alias(c) for c in train_df.columns]).show()
# test_df.select([count(when(isnan(c), c)).alias(c) for c in test_df.columns]).show()

+---+---+-----+------+----+-----+
_c0| id|title|author|text|label|
+---+---+-----+------+----+-----+
 0| 0| 0| 0| 0| 0|
+---+---+-----+------+----+-----+

+---+-----+------+----+
 id|title|author|text|
+---+-----+------+----+
 0| 0| 503| 0|
+---+-----+------+----+

In [0]:
# Null values
train_df = train_df.na.fill("Missing")
# test_df = test_df.na.fill("Missing")

# NA comes in other forms as well
from pyspark.sql.functions import when

train_df = train_df.withColumn("author", \
              when(train_df["author"] == "nan", "Missing").otherwise(train_df["author"]))
train_df = train_df.withColumn("title", \
              when(train_df["title"] == "nan", "Missing").otherwise(train_df["title"]))
train_df = train_df.withColumn("text", \
              when(train_df["text"] == "nan", "Missing").otherwise(train_df["text"]))


In [0]:
print("Number of unique articles in training set: {}".format(train_df.select('id').distinct().count()))
# print("Number of unique articles in test set: {}".format(test_df.select('id').distinct().count()))

Number of unique articles in training set: 20800
Number of unique articles in test set: 5200

### III. Text Preprocessing
- Cleaning the text : remove special characters, URLS, single characters from the start, single characters and words of 3 characters
- Tokenizing the text : Tokenization is the process of demarcating and possibly classifying sections of a string of input characters. 
- Removing the stop words :  Extremely common words, almost useless for them to have much value in analysis
- Text stemming : Extracting the root of the word. Now this is faster than lemmatization which is more time consuming because not only does it extract the root but it also converts it into the nearest noun/verb. I have seen that this does not have a HUGE difference in the final prediction performance, the costs outweigh the benefits.

In [0]:
# Clean text
# Remove all single characters
df_clean = train_df.select(lower(regexp_replace('text', '\s+[a-zA-Z]\s+', " ")).alias('text'), "label")
# Remove single characters from the start
df_clean = df_clean.select(lower(regexp_replace('text', "[^a-zA-Z\\s]", " ")).alias('text'),"label")
# Remove urls
df_clean = df_clean.select(lower(regexp_replace('text', "http\S+|www\S+|https\S+", " ")).alias('text'),"label")
# Remove user @ references and '#' from text
df_clean = df_clean.select(lower(regexp_replace('text', '\@\w+|\#', " ")).alias('text'),"label")
# Remove words of 3 characters
df_clean = df_clean.select(lower(regexp_replace('text', '\b\w{1,3}\b', " ")).alias('text'),"label")

df_clean.show()

+--------------------+-----+
 text|label|
+--------------------+-----+
house dem aide w...| 1|
ever get the feel...| 0|
why the truth mig...| 1|
videos civilia...| 1|
print 
an iranian...| 1|
in these trying t...| 0|
ever wonder how b...| 1|
paris france...| 0|
donald j trump i...| 0|
a week before mic...| 0|
organizing for ac...| 0|
the bbc produced ...| 0|
the mystery surro...| 1|
clinton campaign ...| 1|
yes there are pa...| 1|
guillermo barros ...| 0|
the scandal engul...| 0|
a caddo nation tr...| 1|
fbi closes in on ...| 1|
wednesday after ...| 0|
+--------------------+-----+
only showing top 20 rows

In [0]:
# Tokenize text
tokenizer = Tokenizer(inputCol='text', outputCol='words_token')
df_words_token = tokenizer.transform(df_clean).select('words_token',"label")
df_words_token.show()

+--------------------+-----+
 words_token|label|
+--------------------+-----+
[house, dem, aide...| 1|
[ever, get, the, ...| 0|
[why, the, truth,...| 1|
[videos, , , , ci...| 1|
[print, , an, ira...| 1|
[in, these, tryin...| 0|
[ever, wonder, ho...| 1|
[paris, , , , , ,...| 0|
[donald, j, , tru...| 0|
[a, week, before,...| 0|
[organizing, for,...| 0|
[the, bbc, produc...| 0|
[the, mystery, su...| 1|
[clinton, campaig...| 1|
[yes, , there, ar...| 1|
[guillermo, barro...| 0|
[the, scandal, en...| 0|
[a, caddo, nation...| 1|
[fbi, closes, in,...| 1|
[wednesday, after...| 0|
+--------------------+-----+
only showing top 20 rows

In [0]:
# Remove stop words
remover = StopWordsRemover(inputCol='words_token', outputCol='words_clean')
df_words_no_stopw = remover.transform(df_words_token).select( 'words_clean',"label")
df_words_no_stopw.show()

+--------------------+-----+
 words_clean|label|
+--------------------+-----+
[house, dem, aide...| 1|
[ever, get, feeli...| 0|
[truth, might, ge...| 1|
[videos, , , , ci...| 1|
[print, , iranian...| 1|
[trying, times, ,...| 0|
[ever, wonder, br...| 1|
[paris, , , , , ,...| 0|
[donald, j, , tru...| 0|
[week, michael, ,...| 0|
[organizing, acti...| 0|
[bbc, produced, s...| 0|
[mystery, surroun...| 1|
[clinton, campaig...| 1|
[yes, , paid, gov...| 1|
[guillermo, barro...| 0|
[scandal, engulfi...| 0|
[caddo, nation, t...| 1|
[fbi, closes, hil...| 1|
[wednesday, , , d...| 0|
+--------------------+-----+
only showing top 20 rows

In [0]:
# Stem text
stemmer = SnowballStemmer(language='english')
stemmer_udf = udf(lambda tokens: [stemmer.stem(token) for token in tokens], ArrayType(StringType()))
df_stemmed = df_words_no_stopw.withColumn("words_stemmed", stemmer_udf("words_clean")).select( 'words_stemmed',"label")

df_stemmed.show()

+--------------------+-----+
 words_stemmed|label|
+--------------------+-----+
[hous, dem, aid, ...| 1|
[ever, get, feel,...| 0|
[truth, might, ge...| 1|
[video, , , , civ...| 1|
[print, , iranian...| 1|
[tri, time, , jac...| 0|
[ever, wonder, br...| 1|
[pari, , , , , , ...| 0|
[donald, j, , tru...| 0|
[week, michael, ,...| 0|
[organ, action, ,...| 0|
[bbc, produc, spo...| 0|
[mysteri, surroun...| 1|
[clinton, campaig...| 1|
[yes, , paid, gov...| 1|
[guillermo, barro...| 0|
[scandal, engulf,...| 0|
[caddo, nation, t...| 1|
[fbi, close, hill...| 1|
[wednesday, , , d...| 0|
+--------------------+-----+
only showing top 20 rows

In [0]:
# Filter length word > 3
filter_length_udf = udf(lambda row: [x for x in row if len(x) >= 3], ArrayType(StringType()))
df_final_words = df_stemmed.withColumn('words', filter_length_udf(col('words_stemmed')))
df_final_words = df_final_words.drop("words_stemmed")
df_final_words.show()

+-----+--------------------+
label| words|
+-----+--------------------+
 1|[hous, dem, aid, ...|
 0|[ever, get, feel,...|
 1|[truth, might, ge...|
 1|[video, civilian,...|
 1|[print, iranian, ...|
 0|[tri, time, jacki...|
 1|[ever, wonder, br...|
 0|[pari, franc, cho...|
 0|[donald, trump, s...|
 0|[week, michael, f...|
 0|[organ, action, a...|
 0|[bbc, produc, spo...|
 1|[mysteri, surroun...|
 1|[clinton, campaig...|
 1|[yes, paid, gover...|
 0|[guillermo, barro...|
 0|[scandal, engulf,...|
 1|[caddo, nation, t...|
 1|[fbi, close, hill...|
 0|[wednesday, donal...|
+-----+--------------------+
only showing top 20 rows

We use the count vectorizer  to convert our corpus into a matrix of token counts. This implementation produces a sparse representation of the counts.

In [0]:
from pyspark.ml.feature import CountVectorizer, IDF
vectorizer = CountVectorizer(inputCol="words", outputCol="count_features")
model=vectorizer.fit(df_final_words)
featurized_data = model.transform(df_final_words)

#  IDF is an Estimator which is fit on a dataset and produces an IDFModel. The IDFModel takes feature vectors created using the count vectorizer. Intuitively, it down-weights features which appear frequently in a corpus.
idf = IDF(inputCol="count_features", outputCol="features")
idf_model = idf.fit(featurized_data)
rescaled_data = idf_model.transform(featurized_data)
df_train=rescaled_data.select("features","label")
df_train.show()

+--------------------+-----+
 features|label|
+--------------------+-----+
(109474,[2,5,6,7,...| 1|
(109474,[0,1,2,4,...| 0|
(109474,[2,3,4,5,...| 1|
(109474,[0,2,3,4,...| 1|
(109474,[2,3,5,14...| 1|
(109474,[1,4,6,7,...| 0|
(109474,[2,4,6,7,...| 1|
(109474,[0,2,4,5,...| 0|
(109474,[0,1,2,3,...| 0|
(109474,[0,1,2,3,...| 0|
(109474,[0,1,2,3,...| 0|
(109474,[0,2,3,4,...| 0|
(109474,[0,5,7,11...| 1|
(109474,[1,9,10,1...| 1|
(109474,[0,2,3,4,...| 1|
(109474,[0,2,3,4,...| 0|
(109474,[0,2,5,6,...| 0|
(109474,[0,2,3,4,...| 1|
(109474,[1,2,3,5,...| 1|
(109474,[0,1,2,4,...| 0|
+--------------------+-----+
only showing top 20 rows

### IV. Training the classification models

In [0]:
# set seed for reproducibility
(training_df, testing_df) = rescaled_data.randomSplit([0.8, 0.2], seed = 123)
print("Training dataset Count: " + str(training_df.count()))
print("Test dataset Count: " + str(testing_df.count()))

Training dataset Count: 16563
Test dataset Count: 4237

In [0]:
training_df = training_df.withColumn("label", training_df["label"].cast(IntegerType()))
testing_df = testing_df.withColumn("label", testing_df["label"].cast(IntegerType()))

#### IV.A. Logistic Regression

In [0]:
lr = LogisticRegression(maxIter=20, regParam=0.3, elasticNetParam=0)
lr_model = lr.fit(training_df)
predictions = lr_model.transform(testing_df)


In [0]:
# Checking the predictions for the fake news : prediction ==1
predictions.filter(predictions['prediction'] == 1) \
    .select("words","probability","label","prediction") \
    .orderBy("probability", ascending=False) \
    .show(n = 10, truncate = 30)

+------------------------------+------------------------------+-----+----------+
 words| probability|label|prediction|
+------------------------------+------------------------------+-----+----------+
[french, citizen, kill, mal...|[0.4990571160202238,0.50094...| 1| 1.0|
[sant, cugat, del, vall, sp...|[0.4983373925024321,0.50166...| 0| 1.0|
[tel, aviv, meet, presid, d...|[0.4980272229287568,0.50197...| 0| 1.0|
[plan, parenthood, abort, p...|[0.49710595078819464,0.5028...| 1| 1.0|
[post, octob, paul, joseph,...|[0.494612936090328,0.505387...| 1| 1.0|
[korean, central, news, age...|[0.4935097917180875,0.50649...| 0| 1.0|
[alleg, driver, van, kill, ...|[0.4933723902730611,0.50662...| 0| 1.0|
[new, regent, univers, colo...|[0.49310869825189707,0.5068...| 0| 1.0|
[japanes, prime, minist, sh...|[0.49302905771084937,0.5069...| 0| 1.0|
[averag, american, commut, ...|[0.4929811825835111,0.50701...| 0| 1.0|
+------------------------------+------------------------------+-----+----------+
only showing top 10 rows

#####IV.A.1. Obtaining errors and other evaluation metrics on our model
We see that the recall rate by label = (number of true positives/actual positives) is very high, meaning the false positives are low. We see similar results for the precision (or % of correct attribution) as well.
The accuracy = 0.92 is pretty good meaning the test error is 1-accuracy = 0.08!

In [0]:
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction")
evaluator.evaluate(predictions)

Out[47]: 0.9237206503340443

In [0]:
# Print the coefficients and intercept for multinomial logistic regression
print("Coefficients: \n" + str(lr_model.coefficientMatrix))
print("Intercept: " + str(lr_model.interceptVector))

trainingSummary = lr_model.summary

# Obtain the objective per iteration
objectiveHistory = trainingSummary.objectiveHistory
print("objectiveHistory:")
for objective in objectiveHistory:
    print(objective)

# for multiclass, we can inspect metrics on a per-label basis
print("False positive rate by label:")
for i, rate in enumerate(trainingSummary.falsePositiveRateByLabel):
    print("label %d: %s" % (i, rate))

print("True positive rate by label:")
for i, rate in enumerate(trainingSummary.truePositiveRateByLabel):
    print("label %d: %s" % (i, rate))

print("Precision by label:")
for i, prec in enumerate(trainingSummary.precisionByLabel):
    print("label %d: %s" % (i, prec))

print("Recall by label:")
for i, rec in enumerate(trainingSummary.recallByLabel):
    print("label %d: %s" % (i, rec))


accuracy = trainingSummary.accuracy
falsePositiveRate = trainingSummary.weightedFalsePositiveRate
truePositiveRate = trainingSummary.weightedTruePositiveRate
precision = trainingSummary.weightedPrecision
recall = trainingSummary.weightedRecall
print("Accuracy: %s\nFPR: %s\nTPR: %s\nF-measure: %s\nPrecision: %s\nRecall: %s"
      % (accuracy, falsePositiveRate, truePositiveRate, fMeasure, precision, recall))

Coefficients: 
DenseMatrix([[-0.02368092, -0.00259042, -0.00181572, ..., 0. ,
 0. , 0.00729724]])
Intercept: [1.064371092625835]
objectiveHistory:
0.6931469600250103
0.5630690419579748
0.3570640786568574
0.3242717001996432
0.28967708642312495
0.2679438689923245
0.24647925727009812
0.23620309381549784
0.23398209555743893
0.23271012290473198
0.23200818930804495
0.23073316189266527
0.2299583248402166
0.22894692230436925
0.22743414464653083
0.22610516493375393
0.22400548541128984
0.22214833812359563
0.22061667627145043
0.21949107923112676
0.21867371466262597
False positive rate by label:
label 0: 0.00024134186074574636
label 1: 0.018003866602223296
True positive rate by label:
label 0: 0.9819961333977767
label 1: 0.9997586581392542
Precision by label:
label 0: 0.999753967277648
label 1: 0.982333412378468
Recall by label:
label 0: 0.9819961333977767
label 1: 0.9997586581392542
F-measure by label:
label 0: 0.9907954891801279
label 1: 0.9909694396268165
Accuracy: 0.990883294089235
FPR: 0.009128502552204085
TPR: 0.9908832940892351
F-measure: 0.990882522166405
Precision: 0.991037905063707
Recall: 0.9908832940892351

##### IV.A.2. Tuning hyper parameters
Let’s now try cross-validation to tune our hyper parameters, for the Logistic Regression.

In [0]:
lr = LogisticRegression(maxIter=20, regParam=0.3, elasticNetParam=0)
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
# Create ParamGrid for Cross Validation
paramGrid = (ParamGridBuilder()
             .addGrid(lr.regParam, [0.1, 0.3, 0.5]) # regularization parameter
             .addGrid(lr.elasticNetParam, [0.0, 0.1, 0.2]) # Elastic Net Parameter (Ridge = 0)
#            .addGrid(model.maxIter, [10, 20, 50]) #Number of iterations
             .build())
# Create 5-fold CrossValidator
cv = CrossValidator(estimator=lr, \
                    estimatorParamMaps=paramGrid, \
                    evaluator=evaluator, \
                    numFolds=5)
cvModel = cv.fit(training_df)

predictions = cvModel.transform(testing_df)
# Evaluate best model
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction")
evaluator.evaluate(predictions)

/databricks/spark/python/pyspark/ml/util.py:800: UserWarning: Cannot find mlflow module. To enable MLflow logging, install mlflow from PyPI.
 warnings.warn(_MLflowInstrumentation._NO_MLFLOW_WARNING)
Out[48]: 0.929166561116021

#### IV.B. Random Forest Classifier

In [0]:
rf_1 = RandomForestClassifier(labelCol="label", \
                            featuresCol="features", \
                            numTrees = 100, \
                            maxDepth = 4, \
                            maxBins = 32)
# Train model with Training Data
rf_model_1 = rf_1.fit(training_df)
predictions_1 = rf_model_1.transform(testing_df)
predictions_1.filter(predictions_1['prediction'] == 1) \
    .select("words","probability","label","prediction") \
    .orderBy("probability", ascending=False) \
    .show(n = 10, truncate = 30)

+------------------------------+------------------------------+-----+----------+
 words| probability|label|prediction|
+------------------------------+------------------------------+-----+----------+
[friday, fox, news, channel...|[0.4999768768683154,0.50002...| 0| 1.0|
[save, tax, refund, check, ...|[0.49996116905360594,0.5000...| 0| 1.0|
[wife, disgrac, former, new...|[0.49990537874992436,0.5000...| 0| 1.0|
[michael, schindler, novemb...|[0.49990256918545906,0.5000...| 1| 1.0|
[octob, conserv, claim, vot...|[0.499888377160962,0.500111...| 1| 1.0|
[dean, daniel, novemb, poli...|[0.4998204536707986,0.50017...| 1| 1.0|
[half, voter, think, leak, ...|[0.49972517004630085,0.5002...| 0| 1.0|
[getti, john, shearer, staf...|[0.49949983915331303,0.5005...| 1| 1.0|
[desper, obama, rip, comey,...|[0.4994768373802674,0.50052...| 1| 1.0|
[battl, senat, lead, precip...|[0.4994640874517124,0.50053...| 1| 1.0|
+------------------------------+------------------------------+-----+----------+
only showing top 10 rows

In [0]:
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction")
evaluator.evaluate(predictions_1)

Out[55]: 0.747807517330821

We see for the random forest classifier the accuracy is quite low (meaning error = 1 - accuracy is high).  The plain logistic model outperforms the former as we have sparse high dimensional data. This is why we did not tune the params for the random forest classifer. 

The cross validation search for the best parameters gives us the highest accuracy but it is not a massive improvement from the logistic regression without CV.

## You have reached the end of this notebook